In [1]:
import pyforest
import datetime

### First importing the VIX merged dataset from 01-12-2014 to 14-05-2020

In [2]:
df = pd.read_csv('raw_v2_dataset.csv')
df = df.drop('Unnamed: 0', axis=1)
df.head()

<IPython.core.display.Javascript object>

Date  BTC price [USD]  Volume BTC  Gold price[USD]  \
0  2014-12-01            370.0        0.06           1332.5   
1  2014-12-02            378.0       15.01           1314.7   
2  2014-12-03            378.0        0.55           1325.8   
3  2014-12-04            377.1        0.01           1324.2   
4  2014-12-05            377.1        0.00           1310.8   

   Oil WTI price[USD]  SP500 close index  BTC n-transactions  \
0               68.98            2053.44             79098.0   
1               66.99            2066.55             99419.0   
2               67.30            2074.33             99419.0   
3               66.73            2071.92             99419.0   
4               65.89            2075.37             90900.0   

   BTC google search interest  VIX Close  
0                           3      14.29  
1                           3      12.85  
2                           3      12.47  
3                           3      12.38  
4                           3      11.82

### Checking for the missing values

In [5]:
df.isnull().sum()

Date                          0
BTC price [USD]               0
Volume BTC                    0
Gold price[USD]               0
Oil WTI price[USD]            0
SP500 close index             0
BTC n-transactions            0
BTC google search interest    0
VIX Close                     0
dtype: int64

In [6]:
df.describe()

BTC price [USD]     Volume BTC  Gold price[USD]  Oil WTI price[USD]  \
count      1365.000000    1365.000000      1365.000000         1365.000000   
mean       4169.047451   12266.697355      1343.260916           51.891619   
std        3983.986177   11281.452481       119.471181           11.083033   
min         120.000000       0.000000      1097.700000          -36.980000   
25%         444.880000    6127.140000      1272.400000           46.210000   
50%        3380.010000    8889.980000      1324.200000           52.010000   
75%        7414.080000   14852.080000      1392.100000           58.840000   
max       19039.000000  160540.990000      1768.900000           77.410000   

       SP500 close index  BTC n-transactions  BTC google search interest  \
count        1365.000000         1365.000000                 1365.000000   
mean         2479.272103       242169.406593                   12.325275   
std           379.182688        80382.192997                   14.523708   
min          1829.080000        59344.000000                    2.000000   
25%          2102.440000       193578.000000                    3.000000   
50%          2459.270000       242303.000000                   10.000000   
75%          2793.840000       303632.000000                   15.000000   
max          3386.150000       439549.000000                  100.000000   

         VIX Close  
count  1365.000000  
mean     16.412674  
std       7.913542  
min       9.140000  
25%      12.390000  
50%      14.280000  
75%      17.660000  
max      82.690000

Let's rename the column names for a better usability

In [7]:
df = df.rename(columns = {'Date': 'date', 'BTC price [USD]': 'btc_price', 'Volume BTC':'btc_vol', 'Gold price[USD]':'gold_price',
       'Oil WTI price[USD]':'oil_wti_price', 'SP500 close index':'sp500_close', 'BTC n-transactions':'btc_num_trans',
       'BTC google search interest':'btc_google_search', 'VIX Close':'vix_close'})

## Features we are looking for:

1. Daily Returns : The daily return measures the dollar change in a stock's price as a percentage of the previous day's closing    price. A positive return means the stock has grown in value, while a negative return means it has lost value.

2. Volatility : Volatility is a statistical measure of the dispersion of returns for a given security or market index.

Currently we already have the VIX data from the CBOE portal. Formulas used are:

#### Daily Returns of day 1 = ln(closing price of day 1 / closing price of day 0)

#### Bitcoin 30 days historic volatility denoted by BVOL has been calculated using the formula described in BitMEX website. The gold volatility (GVOL) and Oil volatility (OVOL) has been calculated using the same formula.

In [8]:
def get_daily_returns(df_feat):
    P1 = df_feat[1:].reset_index().drop('index',axis=1)
    P0 = df_feat[:-1].reset_index().drop('index', axis=1)
    feat_daily_returns = np.log(P1.div(P0))
    feat_daily_returns.loc[-1] = 0
    feat_daily_returns.index = feat_daily_returns.index + 1
    feat_daily_returns = feat_daily_returns.sort_index()

    return feat_daily_returns


def get_volatility(ln_twap_ratio):
    feat_vol = np.array(0)
    ind = np.array(0)
    for i in range(2,len(ln_twap_ratio)-29):
        feat_vol = np.append(feat_vol, np.std(ln_twap_ratio[i:i+31], ddof=1) * np.sqrt(365))
        ind = np.append(ind, i+29)
    
    feat_vol = np.delete(feat_vol, 0)
    ind = np.delete(ind, 0)
    return feat_vol, ind

In [9]:
df['btc_dr'] = get_daily_returns(df['btc_price'])
df['gold_dr'] = get_daily_returns(df['gold_price'])
df['oil_dr'] = get_daily_returns(df['oil_wti_price'])
df['sp500_dr'] = get_daily_returns(df['sp500_close'])

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<ipython-input-8-4e0fc79d115f>:4: RuntimeWarning: invalid value encountered in log
  feat_daily_returns = np.log(P1.div(P0))


<IPython.core.display.Javascript object>

In [10]:
df.head()

date  btc_price  btc_vol  gold_price  oil_wti_price  sp500_close  \
0  2014-12-01      370.0     0.06      1332.5          68.98      2053.44   
1  2014-12-02      378.0    15.01      1314.7          66.99      2066.55   
2  2014-12-03      378.0     0.55      1325.8          67.30      2074.33   
3  2014-12-04      377.1     0.01      1324.2          66.73      2071.92   
4  2014-12-05      377.1     0.00      1310.8          65.89      2075.37   

   btc_num_trans  btc_google_search  vix_close    btc_dr   gold_dr    oil_dr  \
0        79098.0                  3      14.29  0.000000  0.000000  0.000000   
1        99419.0                  3      12.85  0.021391 -0.013448 -0.029273   
2        99419.0                  3      12.47  0.000000  0.008408  0.004617   
3        99419.0                  3      12.38 -0.002384 -0.001208 -0.008506   
4        90900.0                  3      11.82  0.000000 -0.010171 -0.012668   

   sp500_dr  
0  0.000000  
1  0.006364  
2  0.003758  
3 -0.001162  
4  0.001664

### Importing the raw dataset of bitcoin price movements acquired from Coindesk portal

In [11]:
df_btc = pd.read_csv('bitcoin_raw.csv')
df_btc['Date'] = pd.to_datetime(df_btc['Date'])
df_btc.head()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Currency       Date  Closing Price (USD)  24h Open (USD)  24h High (USD)  \
0      BTC 2013-10-01            123.65499       124.30466       124.75166   
1      BTC 2013-10-02            125.45500       123.65499       125.75850   
2      BTC 2013-10-03            108.58483       125.45500       125.66566   
3      BTC 2013-10-04            118.67466       108.58483       118.67500   
4      BTC 2013-10-05            121.33866       118.67466       121.93633   

   24h Low (USD)  
0      122.56349  
1      123.63383  
2       83.32833  
3      107.05816  
4      118.00566

In [12]:
weekdays = df[['date', 'vix_close']]
weekdays['date'] = pd.to_datetime(weekdays['date'])
weekdays = weekdays.rename(columns={'date':'Date'})
weekdays.head()

<IPython.core.display.Javascript object>

<ipython-input-12-824631852272>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  weekdays['date'] = pd.to_datetime(weekdays['date'])


Date  vix_close
0 2014-12-01      14.29
1 2014-12-02      12.85
2 2014-12-03      12.47
3 2014-12-04      12.38
4 2014-12-05      11.82

### Taking left join to split out all those rows which are not in the base dataset

In [13]:
df_btc_weekdays = pd.merge(df_btc, weekdays, how='left', on='Date')
df_btc_weekdays.dropna(inplace=True)
df_btc_weekdays.reset_index(drop=True, inplace=True)
df_btc_weekdays = df_btc_weekdays.drop(columns=['Currency', 'vix_close'])
df_btc_weekdays.dtypes

<IPython.core.display.Javascript object>

Date                   datetime64[ns]
Closing Price (USD)           float64
24h Open (USD)                float64
24h High (USD)                float64
24h Low (USD)                 float64
dtype: object

### TWAP deals in time calculations. It will calculate the average price of a financial asset (security) over a specified and short period of time.

It'll be used in finding the VOL's of Bitcoin, Gold and Oil

In [14]:
df_btc_weekdays['twap'] = df_btc_weekdays.mean(axis=1, numeric_only=True)
df_btc_weekdays['ln_twap_ratio'] = get_daily_returns(df_btc_weekdays['twap'])
vol_btc, ind_btc = get_volatility(df_btc_weekdays['ln_twap_ratio'])
bvol = pd.DataFrame(data=vol_btc, index=ind_btc, columns=['BVOL'])

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Importing the raw gold price movement dataset acquired from World Gold Council

In [15]:
df_gold = pd.read_csv('gold_df.csv')
df_gold['Date'] = pd.to_datetime(df_gold['Date'])
df_gold = df_gold.sort_values('Date', ignore_index=True)
df_gold.head()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Date     Price      Open      High       Low Volume    Chg%
0 2014-12-01  1,332.50  1,160.00  1,220.40  1,141.70  5.52K   3.20%
1 2014-12-02  1,314.70  1,212.30  1,212.30  1,191.30  1.24K  -1.34%
2 2014-12-03  1,325.80  1,198.10  1,213.70  1,196.10  0.44K   0.84%
3 2014-12-04  1,324.20  1,208.20  1,213.00  1,201.60  0.36K  -0.12%
4 2014-12-05  1,310.80  1,203.10  1,206.00  1,186.70  0.56K  -1.01%

In [16]:
df_gold[df_gold['Date']== '2020-05-14']

Date     Price      Open      High       Low Volume   Chg%
1443 2020-05-14  1,762.00  1,743.30  1,765.10  1,735.00  4.05K  1.42%

### Splitting the dateset for required date range

In [17]:
df_gold = df_gold[:1444][:]
df_gold_weekdays = pd.merge(df_gold, weekdays, how='left', on='Date')
df_gold_weekdays.dropna(inplace=True)
df_gold_weekdays.reset_index(drop=True, inplace=True)
df_gold_weekdays = df_gold_weekdays.drop(columns=['Chg%', 'vix_close', 'Volume'])

<IPython.core.display.Javascript object>

### This function will be used to clean the gold dataset

In [18]:
def clean_currency(x):
    if isinstance(x, str):
        return(x.replace(',', ''))
    return(x)

In [20]:
df_gold_weekdays['Price'] = df_gold_weekdays['Price'].apply(clean_currency).astype('float')
df_gold_weekdays['Open'] = df_gold_weekdays['Open'].apply(clean_currency).astype('float')
df_gold_weekdays['High'] = df_gold_weekdays['High'].apply(clean_currency).astype('float')
df_gold_weekdays['Low'] = df_gold_weekdays['Low'].apply(clean_currency).astype('float')
df_gold_weekdays[['Price', 'Open', 'High', 'Low']] = df_gold_weekdays[['Price', 'Open', 'High', 'Low']].astype(float)
df_gold_weekdays['twap'] = df_gold_weekdays.mean(axis=1,numeric_only=True)

df_gold_weekdays['ln_twap_ratio'] = get_daily_returns(df_gold_weekdays['twap'])
vol_gold, ind_gold = get_volatility(df_gold_weekdays['ln_twap_ratio'])
gvol = pd.DataFrame(data=vol_gold, index=ind_gold, columns=['GVOL'])

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Now let's calculate the Oil price Volatility
Oil Prices have been acquired from Yahoo Finance

In [22]:
df_oil = pd.read_csv('oil_price_raw.csv', parse_dates=True)
df_oil.head()

<IPython.core.display.Javascript object>

Date       Open       High        Low      Close  Adj Close    Volume
0  2014-12-01  66.000000  69.540001  63.720001  69.000000  69.000000  504122.0
1  2014-12-02  69.239998  69.320000  66.669998  66.879997  66.879997  360300.0
2  2014-12-03  67.599998  68.230003  66.800003  67.379997  67.379997  293483.0
3  2014-12-04  67.400002  68.220001  66.089996  66.809998  66.809998  237011.0
4  2014-12-05  66.800003  66.889999  65.169998  65.839996  65.839996  276529.0

In [23]:
df_oil['Date'] = pd.to_datetime(df_oil['Date'])
df_oil.drop(['Adj Close', 'Volume'], axis=1, inplace=True)
df_oil_weekdays = pd.merge(df_oil, weekdays, how='left', on='Date')
df_oil_weekdays.dropna(inplace=True)
df_oil_weekdays.reset_index(drop=True, inplace=True)
df_oil_weekdays = df_oil_weekdays.drop(columns='vix_close')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

#### On 20th and 21st April 2020, the crude oil prices dropped to a negative value for the first time
So, let's remove these two outliers as they can affect our model performance

In [24]:
df_oil_weekdays.drop(index=[1335,1336], inplace=True)

In [25]:
df_oil_weekdays['twap'] = df_oil_weekdays.mean(axis=1, numeric_only=True)
df_oil_weekdays['ln_twap_ratio'] = get_daily_returns(df_oil_weekdays['twap'])
vol_oil, ind_oil = get_volatility(df_oil_weekdays['ln_twap_ratio'])
ovol = pd.DataFrame(data=vol_oil, index=ind_oil, columns=['OVOL'])

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## Preparing final dataset

In [41]:
df_final = pd.concat([df, bvol, gvol, ovol], axis=1)

<IPython.core.display.Javascript object>

In [42]:
df_final.dropna(inplace=True)

In [45]:
df_final.reset_index(drop=True, inplace=True)
df_final.rename(columns={'vix_close':'VIX'}, inplace=True)

In [47]:
df_final = df_final[['date', 'btc_price', 'gold_price', 'oil_wti_price', 'sp500_close', 'btc_num_trans', 'btc_google_search','btc_dr','gold_dr','oil_dr','sp500_dr','BVOL','GVOL','OVOL','VIX']]

In [49]:
df_final.head()

date  btc_price  gold_price  oil_wti_price  sp500_close  \
0  2015-01-15     211.91      1352.8          46.37      1992.67   
1  2015-01-16     199.46      1364.9          48.49      2019.42   
2  2015-01-20     208.00      1377.4          46.79      2022.55   
3  2015-01-21     225.51      1378.4          47.85      2032.12   
4  2015-01-22     226.32      1390.2          45.93      2063.15   

   btc_num_trans  btc_google_search    btc_dr   gold_dr    oil_dr  sp500_dr  \
0       102309.0                  3  0.568670  0.021141 -0.044705 -0.009291   
1       104699.0                  3 -0.060548  0.008905  0.044705  0.013335   
2        98485.0                  3  0.041924  0.009116 -0.035688  0.001549   
3        98485.0                  3  0.080826  0.000726  0.022402  0.004720   
4        93698.0                  3  0.003585  0.008524 -0.040953  0.015154   

       BVOL      GVOL      OVOL    VIX  
0  0.853974  0.344132  0.344950  22.39  
1  0.857286  0.348453  0.346061  20.95  
2  0.857176  0.348518  0.346647  19.89  
3  0.893605  0.350149  0.347336  18.85  
4  0.904949  0.351242  0.343230  16.40

#### Exporting the csv file

In [50]:
df_final.to_csv('dataset_final.csv')